In [1]:
!pip -q install git+https://github.com/huggingface/transformers.git
!pip -q install peft
!pip -q install accelerate
!pip -q install sentencepiece
!pip -q install bitsandbytes

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 18.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 49.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 23.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 59.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 16.4 MB/s eta 0:00:00


In [2]:
from IPython.display import Markdown as md

import transformers
import peft
import accelerate
import bitsandbytes

print(transformers.__version__)
print(peft.__version__)
print(accelerate.__version__)



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so.11.0
CUDA SETUP: Highest compute capability among GPUs detected: 8.0
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('http'), PosixPath('//172.28.0.1'), PosixPath('8013')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc483011

4.29.0.dev0
0.2.0
0.18.0


In [3]:
import torch
from peft import PeftModel
from transformers import LlamaTokenizer, LlamaForCausalLM

def load_model(base, finetuned):
    tokenizer = LlamaTokenizer.from_pretrained(base)
    tokenizer.pad_token_id = 0
    tokenizer.padding_side = "left"

    model = LlamaForCausalLM.from_pretrained(
        base,
        load_in_8bit=True,
        device_map="auto",
    )
    
    model = PeftModel.from_pretrained(
        model, 
        finetuned,
        device_map={'': 0}
    )
    return model, tokenizer

def get_output_batch(
    model, tokenizer, prompt, generation_config, device='cuda'
):
  encoding = tokenizer(prompt, return_tensors="pt")
  input_ids = encoding["input_ids"].to(device)
  generated_id = model.generate(
      input_ids=input_ids,
      generation_config=generation_config,
  )

  decoded = tokenizer.batch_decode(
      generated_id, skip_prompt=True, skip_special_tokens=True
  )
  del input_ids, generated_id
  torch.cuda.empty_cache()
  return decoded[0].split("### Response:")[-1]

### AlpacaGPT4-LoRA 13B (05/01)

In [4]:
from transformers import GenerationConfig

base = "elinas/llama-13b-hf-transformers-4.29"
sft = "LLMs/AlpacaGPT4-LoRA-13B-elina"

genConfig = GenerationConfig(
    temperature=0.95,
    top_p=0.9,
    top_k=50,
    num_beams=1,
    repetition_penalty=1.2,
    max_new_tokens=1024,
    do_sample=True,
)

In [5]:
model, tokenizer = load_model(base, sft)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [6]:
prompt = """### Instruction: Compose an engaging travel blog post about a recent trip to Hawaii, highlighting cultural experiences and must-see attractions.

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />I recently took the journey of my lifetime - a weeklong adventure through one of nature's most beautiful creations: Hawaii! I had heard so much about this magical island paradise before going but nothing could prepare me for how truly breathtaking it was in real life. From hiking along verdant mountain trails to swimming with turtles beneath clear turquoise waters, every moment felt like something out of a fairytale. But above all else, what made our visit to Hawaii so memorable were its rich culture and traditions that we experienced firsthand.<br /><br />One of the highlights of our time there was learning more about Native Hawaiian culture at Puuhonua O Honaunau National Historical Park, also known as "the place of refuge." Here, ancient laws were upheld which allowed wrongdoers who broke certain rules or protocols (like stealing) the chance for redemption if they reached the sacred grounds within 24 hours. This history is fascinating to learn about, particularly since many aspects of traditional Hawaiian culture are still very alive today. The park offers guided tours led by passionate volunteer tour guides who give great insight into the significance behind each feature on site, such as the sacred temple and carved stones called ki‘is. You can even participate in ceremonies held here on special occasions throughout the year. It's not often you get to connect with a destination’s history and heritage in such an intimate way – definitely don’t miss out on this unique opportunity when planning your own trip!<br /><br />Another unforgettable experience was enjoying some local cuisine. We tried shave ice and malasadas from the famous Leonard's Bakery right near the airport after landing in Honolulu. These iconic desserts have been delighting visitors for years, and it doesn't take long to see why – the delicate flavors of strawberry, vanilla, and coconut will leave you craving more. Later during our stay, we headed to Old Lahaina Luau located just outside Maui to partake in their signature Polynesian feast. Enjoy live entertainment while dining on Kalua pig cooked underground for eight whole hours and poi prepared using sweet potatoes instead of kalo. To top things off, indulge in fresh fruits like mangoes, papaya, and pineapples, sourced straight from Hawaiian farms and delivered daily. Overall, it was the perfect introduction to Hawaiian food, full of bright colors, complex textures, and bold flavor combinations that left us feeling happy and satisfied.<br /><br />The final experience that really stood out for me was visiting Pipiwai Trail at Kipuka Mahoe State Monument, accessible via Waimoku Falls Trailhead. While driving up winding roads flanked by lush green jungle foliage, we couldn't help but be awestruck by the beauty surrounding us. Eventually reaching the trailhead, we embarked upon the hike itself, passing by cascading waterfalls, peaceful pools, and towering bamboos. After several miles, we arrived at a large open field filled with colorful flowers, where we saw locals setting up picnic blankets alongside wild chickens pecking away at seeds scattered around them. There's no better way to end a day than relaxing amidst nature and taking in everything she has to offer. We spent over three hours exploring the entire area before making our way back down, grateful for the serene atmosphere and stunning scenery we had encountered along the way.<br /><br />Overall, our trip to Hawaii lived up to expectations and then some! Every aspect of this wonderful destination was beyond captivating - from natural landscapes to vibrant cultures and cuisines - making it impossible not to fall in love. So if you ever find yourself dreaming of escape to a tropical paradise, book your ticket now because once you go, you won’t want to come home. Aloha!

In [7]:
prompt = """### Instruction: Can you help me write a formal email to a potential business partner proposing a joint venture?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Potential Business Partner], <br />Greetings!<br /><br />I am writing this message on behalf of my company, which specializes in providing market analysis services. Our aim is to use our extensive experience and knowledge in the industry to deliver exceptional results for customers worldwide. We are seeking new opportunities to expand our operations by forming strategic partnerships with companies like yours that share similar objectives. It was brought to my attention that your organization has a proven track record in customer satisfaction and quality assurance within its own area of expertise. This makes us believe there may be significant synergies between both entities when it comes to working together towards mutually beneficial outcomes. I propose we explore the possibilities of a long-term cooperation that would allow each party to bring their unique skill sets into play while taking advantage of the other's strengths. <br />Our goal will be to provide top notch analysis of current trends and emerging markets, while also bringing about improved efficiency to all our clients. Your input and involvement will no doubt add value to such an endeavor. With these thoughts in mind, let’s get started exploring what could become an effective collaboration opportunity for both parties involved. Please feel free to contact me anytime if you have questions or need additional information from my end.

In [8]:
prompt = """### Instruction: Can you help me write a resignation letter to my current employer, while leaving on good terms and expressing gratitude for the opportunities provided?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Supervisor Name],<br /><br />I am writing this letter as an official notice of my intent to leave my position at your company. My last day with the organization will be [insert date]. Throughout the course of my time here I have had some wonderful experiences working in this team and I want to thank you all personally for that opportunity. It has been truly rewarding to work alongside such a talented group of individuals.<br /><br />It is not easy for me to part ways with colleagues who feel like family but after careful consideration I believe it's best if we move our separate paths forward.<br /><br />Thank you once again for providing me with valuable career growth and development over these past few years and wish nothing but success for every single one of us going forward.

In [9]:
prompt = """### Instruction: How can you determine if a restaurant is popular among locals or mainly attracts tourists, and why might this information be useful?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />One way to tell the difference between local patrons versus tourist-focused restaurants could be through examining their online reviews. Local review sites such as Yelp, Google Maps or Tripadvisor will provide valuable insight into customer satisfaction of diners who live in that area compared with out-of town visitors whose interests are more focused on exploring new places rather than finding long term favorites. The language used by customers to describe the experience at these two types of restaurants may also differ; for instance, “tourist trap” could indicate that a place primarily caters to people passing through rather than regulars looking for authentic food experiences. Additionally, researching how frequently certain dishes appear on menus would give clues about which cuisines appeal specifically to foreign travelers vs. regional residents. This type of data gathering and analysis provides a deeper understanding of what kind of patronage any given eatery enjoys and allows businesses to tailor marketing strategies accordingly.

In [10]:
prompt = """### Instruction: What are some subtle clues that suggest someone is pretending to understand a topic or conversation when they are actually confused or uninformed?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />1. They ask for clarification frequently, sometimes with redundancy - "Wait... you mean like this?" <br />2. Their body language becomes increasingly tense and strained as the discussion progresses.<br />3. They resort to vague statements in place of direct answers, such as saying "I think so" rather than giving their own opinion.<br />4. When faced with challenging questions, instead of responding directly, they give vague responses which seem more focused on avoidance, such as answering by saying something about themselves ("Oh I know what you mean! That's exactly how I felt last week") without addressing the question at hand.<br />5. They repeat buzzwords and common phrases while failing to expand on them, often accompanied by an intense nodding gesture even though it doesn't appear they really understand.<br />6. While appearing engaged during conversations, they fail to demonstrate any sort of understanding or comprehension through their facial expressions, gestures or comments made afterward.

In [11]:
prompt = """### Instruction: What are some potential implications of using a single-use plastic bottle versus a reusable bottle on both the environment and human health?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 Using a single-use plastic bottle instead of a reusable one has various negative impacts on our ecosystem, as well as public health. Some key concerns are outlined below: <br />1. Plastics waste in landfills - The accumulation of single use water bottles is rapidly growing, with an estimated 30 billion being thrown away every year worldwide [1]. In addition to the obvious visual pollution that accompanies discarded plastics littering the streets, these objects take up valuable space in already overcrowded landfill sites, where they may remain for hundreds or thousands of years before breaking down into smaller pieces [2][3]. Once released into nature from the site, these microplastics can be carried by wind and rivers and eventually make their way into the ocean, harming aquatic life and entering the food chain [4]. Even when incinerated, burning plastics releases hazardous chemical compounds such as benzo(a)pyrene, known carcinogens[5], and polycyclic aromatic hydrocarbons (PAHs), which are mutagenic and toxic to humans at high doses.[6] Thus, the presence of large quantities of plastics not only detract from the natural beauty of surroundings but also pose significant risks to the health of living organisms and ultimately us.<br />2. Petroleum usage - The production of most plastics requires crude oil, a finite resource which is extracted through dangerous methods like hydraulic fracturing ('fracking')[7],[8].[9] Additionally, petrochemical manufacture contributes significantly to air pollutants including carbon dioxide emissions[10](CO2), nitrous oxides ([NOX])and sulfur dioxides([SO2]). These greenhouse gases contribute to climate change, causing sea level rise, more intense storms, droughts and heat waves[11]. Given its ubiquity across industries and products, reducing plastic consumption represents an important step toward mitigating the damage caused by fossil fuels extraction and utilization. Furthermore, lessening demand for plastic items will reduce pressure on companies to seek new sources of raw material, potentially curbing deforestation[12].<br />3. Chemical leaching - Many types of plastics contain additives like Bisphenol A (BPAs)[13]that have been linked to hormonal imbalances, infertility and even certain types of cancer upon chronic exposure [14]. Reports show that BPS, used as a replacement for BPA in some consumer goods,[15]is just as harmful[16]; thus the cycle continues. With each use and subsequent disposal, the chemical components within the plastic migrate, seeping into soil and groundwater and finally finding their way into our bodies either via ingestion or contact with skin or breathing. Ultimately, this creates greater risk for long term disease development.<br />4. Impact on wildlife - Animals often mistake plastic debris for food, consuming it without realizing the danger[17]. This results in obstructions, injuries and death due to starvation. For instance, fish commonly mistake bits of floating plastic for zooplankton, which they feed on, mistaking them for actual prey [18]. Marine animals and birds consume pieces of plastic mistakenly thinking they're jellyfish [19][20], clogging vital organs. Turtles are particularly prone to entanglement and suffocation because plastic bags resemble Jellyfish [21], while balloons appear attractive to monkeys who unknowingly swallow them, leading to painful digestive issues [22][23]. All in all, plastics cause unnecessary suffering to innocent creatures simply trying to survive.<br />In conclusion, although single-use plastic bottles seem convenient at first glance, their effects on our planet and health far outweigh any benefits. By making responsible choices and switching to alternatives like stainless steel, glass or aluminium, we can collectively help slow the pace of environmental destruction and improve overall quality of life for ourselves and future generations.

In [12]:
prompt = """### Instruction: What factors would you consider when designing an inclusive and accessible public transportation system?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 When designing a more inclusive and accessible public transit, there are several key components to take into account. These include: <br /><br />1) Physical accessibility for people with disabilities such as wheelchair ramps or lifts in vehicles; <br />2) Communications systems that provide information on routes, schedules, stops and alerts in multiple formats (e.g., braille, audio, large print); <br />3) Safe and secure infrastructure including cameras, lighting, security staff/services at bus stations and trains stations;<br />4) Service animals policy – ensuring people travel with their service animals without discrimination;<br />5) Accessible fare payment options - this includes physical ticket vending machines which can be used by visually impaired customers, pre-paid cards and cashless payments (such as NFC/contactless cards), mobile app integrating with the ticket validation process etc.;<br />6) Information about how the transportation network functions and relevant rules e.g., boarding etiquette and protocol, behaviour guidelines during emergencies or evacuations, policies around bringing food and drink onto the vehicle, luggage limitations etc..<br />7) Training of all personnel working within the transit agency on providing services to passengers with various needs, sensitivity towards individuals with disability, awareness of safety measures and protocols during crisis situations involving persons with disability etc.